# ImSpiRE: <ins>Im</ins>age-aided <ins>Sp</ins>at<ins>i</ins>al <ins>R</ins>esolution <ins>E</ins>nhancement

## This is a tutorial written using Jupyter Notebook.

### Step 1. ImSpiRE installation following the [tutorial](XXX).

### Step 2. Input preparation

ImSpiRE utilizes the count file in tab-delimited format or hierarchical-data format (HDF5 or H5) and the image file in TIFF format, as well as a file containing spot coordinates as input. 

We provided a small [test dataset](XXX) containing the raw count matrix, image and spot coordinates. A CellProfiler pipeline is also included in the test dataset for use if required.

### Step 3. Operation of ImSpiRE

### 3.1 Load required packages

In [1]:
import imspire_object as imspire
import pandas as pd
import numpy as np
import scanpy as sc

/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper


### 3.2 Custom parameters

In [2]:
imspire_param=imspire.ImSpiRE_Parameters()

In [3]:
imspire_param.BasicParam_InputCountFile="test_data/count_matrix.tsv"
imspire_param.BasicParam_InputDir="test_data/"
imspire_param.BasicParam_InputImageFile="test_data/image.tif"
imspire_param.BasicParam_PlatForm="ST"
imspire_param.BasicParam_Mode=2
imspire_param.BasicParam_OutputName="test_output"
imspire_param.BasicParam_Overwriting=True
imspire_param.CellProfilerParam_Pipeline="test_data/Cellprofiler_Pipeline_HE.cppipe"

### 3.3 Run ImSpiRE

#### 3.3.1 step by step

In [4]:
imspire.create_folder(imspire_param.BasicParam_OutputDir,
                      imspire_param.BasicParam_OutputName,
                      imspire_param.BasicParam_Overwriting)

In [5]:
imdata=imspire.ImSpiRE_Data()
imdata.read_ST(imspire_param.BasicParam_InputDir, count_file=imspire_param.BasicParam_InputCountFile)

In [6]:
## optional
imdata.preprocess(min_counts=imspire_param.Threshold_MinCounts, 
                  max_counts=imspire_param.Threshold_MaxCounts, 
                  pct_counts_mt=imspire_param.Threshold_MitoPercent, 
                  min_cells=imspire_param.Threshold_MinSpot)

In [7]:
im=imspire.ImSpiRE_HE_Image(imspire_param.BasicParam_InputImageFile,
                            imspire_param.BasicParam_PlatForm,
                            imspire_param.BasicParam_OutputDir,
                            imspire_param.BasicParam_OutputName,
                            imspire_param.FeatureParam_IterCount)

In [8]:
spot_image_output_path=f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/ImageResults/SpotImage"
im.segment_spot_image(pos_in_tissue_filter=imdata.pos_in_tissue_filter,
                      output_path=spot_image_output_path,
                      crop_size=imspire_param.ImageParam_CropSize)

In [9]:
patch_image_output_path=f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/ImageResults/PatchImage"
im.generate_patch_locations_2(pos_in_tissue=imdata.pos_in_tissue_filter,
                              dist=imspire_param.ImageParam_PatchDist)
im.segment_patch_image(patch_in_tissue=im.patch_in_tissue, 
                       output_path=patch_image_output_path, 
                       crop_size=imspire_param.ImageParam_CropSize)

.//test_output/SupplementaryResults/bgremover_output.png


In [10]:
spot_cp=imspire.ImSpiRE_HE_CellProfiler(image_file_path=f"{spot_image_output_path}", 
                                        cellprofiler_pipeline=imspire_param.CellProfilerParam_Pipeline)
patch_cp=imspire.ImSpiRE_HE_CellProfiler(image_file_path=f"{patch_image_output_path}", 
                                         cellprofiler_pipeline=imspire_param.CellProfilerParam_Pipeline)

In [11]:
spot_feature_output_path=f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/FeatureResults/SpotFeature"
spot_cp.compute_image_features(output_path=spot_feature_output_path,
                               number_of_kernels=imspire_param.CellProfilerParam_KernelNumber)
spot_cp.filter_image_features(output_path=spot_feature_output_path)

/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper
Experiment-wide values for mean threshold, etc calculated by MeasureImageQuality may be incorrect if the run is split into subsets of images.
/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper
Experiment-wide values for mean threshold, etc c

Fri Jan  6 11:00:04 2023: Image # 89, module NamesAndTypes # 3: CPU_time = 1.57 secs, Wall_time = 0.83 secs
Fri Jan  6 11:00:05 2023: Image # 89, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:04 2023: Image # 45, module NamesAndTypes # 3: CPU_time = 1.64 secs, Wall_time = 0.91 secs
Fri Jan  6 11:00:05 2023: Image # 45, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:04 2023: Image # 67, module NamesAndTypes # 3: CPU_time = 1.59 secs, Wall_time = 0.86 secs
Fri Jan  6 11:00:05 2023: Image # 67, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:04 2023: Image # 34, module NamesAndTypes # 3: CPU_time = 1.51 secs, Wall_time = 0.83 secs
Fri Jan  6 11:00:05 2023: Image # 34, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 45, module MeasureImageIntensity # 5: CPU_time = 0.04 secs, Wall_time = 0.02 secs
Fri Jan  6 11:00:05 2023: Image # 89, module Mea

Fri Jan  6 11:00:05 2023: Image # 100, module MeasureTexture # 7: CPU_time = 2.67 secs, Wall_time = 0.37 secs
Fri Jan  6 11:00:05 2023: Image # 100, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 100, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 101, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 101, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 46, module NamesAndTypes # 3: CPU_time = 1.30 secs, Wall_time = 0.46 secs
Fri Jan  6 11:00:05 2023: Image # 46, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:05 2023: Image # 46, module MeasureImageIntensity # 5: CPU_time = 0.11 secs, Wall_time = 0.06 secs
Fri Jan  6 11:00:05 2023: Image # 2, module NamesAndTypes # 3: CPU_time = 1.38 secs, Wall_time = 0.48 secs
Fri Jan  6 11:00:06 2023:

Fri Jan  6 11:00:06 2023: Image # 101, module MeasureTexture # 7: CPU_time = 3.79 secs, Wall_time = 0.63 secs
Fri Jan  6 11:00:07 2023: Image # 101, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:07 2023: Image # 101, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:07 2023: Image # 102, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:07 2023: Image # 102, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:07 2023: Image # 3, module MeasureImageQuality # 6: CPU_time = 0.15 secs, Wall_time = 0.13 secs
Fri Jan  6 11:00:07 2023: Image # 80, module NamesAndTypes # 3: CPU_time = 1.11 secs, Wall_time = 0.40 secs
Fri Jan  6 11:00:07 2023: Image # 80, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:07 2023: Image # 91, module NamesAndTypes # 3: CPU_time = 0.85 secs, Wall_time = 0.43 secs
Fri Jan  6 11:00:07 2023: I

Fri Jan  6 11:00:08 2023: Image # 92, module NamesAndTypes # 3: CPU_time = 0.72 secs, Wall_time = 0.48 secs
Fri Jan  6 11:00:08 2023: Image # 92, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:08 2023: Image # 70, module MeasureImageIntensity # 5: CPU_time = 0.12 secs, Wall_time = 0.10 secs
Fri Jan  6 11:00:08 2023: Image # 92, module MeasureImageIntensity # 5: CPU_time = 0.05 secs, Wall_time = 0.10 secs
Fri Jan  6 11:00:08 2023: Image # 102, module MeasureTexture # 7: CPU_time = 6.75 secs, Wall_time = 0.67 secs
Fri Jan  6 11:00:09 2023: Image # 102, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:09 2023: Image # 102, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:09 2023: Image # 103, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:09 2023: Image # 103, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00

...

Fri Jan  6 11:00:12 2023: Image # 16, module MeasureTexture # 7: CPU_time = 6.24 secs, Wall_time = 0.70 secs
Fri Jan  6 11:00:13 2023: Image # 16, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:13 2023: Image # 16, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:13 2023: Image # 17, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:13 2023: Image # 17, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:13 2023: Image # 50, module MeasureImageIntensity # 5: CPU_time = 0.05 secs, Wall_time = 0.08 secs
Fri Jan  6 11:00:13 2023: Image # 106, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.10 secs
Fri Jan  6 11:00:13 2023: Image # 95, module MeasureImageQuality # 6: CPU_time = 0.28 secs, Wall_time = 0.25 secs
Fri Jan  6 11:00:13 2023: Image # 50, module MeasureImageQuality # 6: CPU_time = 0.17 secs, Wall_time = 0.16 secs
F

Fri Jan  6 11:00:14 2023: Image # 8, module MeasureImageIntensity # 5: CPU_time = 0.04 secs, Wall_time = 0.03 secs
Fri Jan  6 11:00:14 2023: Image # 51, module NamesAndTypes # 3: CPU_time = 0.70 secs, Wall_time = 0.20 secs
Fri Jan  6 11:00:14 2023: Image # 51, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:14 2023: Image # 63, module NamesAndTypes # 3: CPU_time = 0.74 secs, Wall_time = 0.31 secs
Fri Jan  6 11:00:14 2023: Image # 63, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:14 2023: Image # 18, module NamesAndTypes # 3: CPU_time = 0.52 secs, Wall_time = 0.18 secs
Fri Jan  6 11:00:14 2023: Image # 18, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:14 2023: Image # 8, module MeasureImageQuality # 6: CPU_time = 0.14 secs, Wall_time = 0.08 secs
Fri Jan  6 11:00:14 2023: Image # 63, module MeasureImageIntensity # 5: CPU_time = 0.03 secs, Wall_time = 0.04 secs
Fri Jan  6 11:00:14 2023: Ima

Fri Jan  6 11:00:15 2023: Image # 42, module MeasureImageQuality # 6: CPU_time = 0.08 secs, Wall_time = 0.06 secs
Fri Jan  6 11:00:15 2023: Image # 64, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:15 2023: Image # 31, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:15 2023: Image # 64, module MeasureImageIntensity # 5: CPU_time = 0.10 secs, Wall_time = 0.05 secs
Fri Jan  6 11:00:15 2023: Image # 52, module NamesAndTypes # 3: CPU_time = 0.65 secs, Wall_time = 0.31 secs
Fri Jan  6 11:00:15 2023: Image # 52, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:15 2023: Image # 97, module NamesAndTypes # 3: CPU_time = 0.84 secs, Wall_time = 0.38 secs
Fri Jan  6 11:00:15 2023: Image # 97, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:15 2023: Image # 31, module MeasureImageIntensity # 5: CPU_time = 0.05 secs, Wall_time = 0.07 secs
Fri Jan  6 11:00:15 2023: Image # 

Fri Jan  6 11:00:16 2023: Image # 53, module NamesAndTypes # 3: CPU_time = 0.74 secs, Wall_time = 0.37 secs
Fri Jan  6 11:00:16 2023: Image # 53, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:16 2023: Image # 53, module MeasureImageIntensity # 5: CPU_time = 0.04 secs, Wall_time = 0.02 secs
Fri Jan  6 11:00:16 2023: Image # 77, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.12 secs
Fri Jan  6 11:00:16 2023: Image # 85, module MeasureTexture # 7: CPU_time = 9.33 secs, Wall_time = 0.51 secs
Fri Jan  6 11:00:16 2023: Image # 10, module MeasureTexture # 7: CPU_time = 4.61 secs, Wall_time = 0.36 secs
Fri Jan  6 11:00:16 2023: Image # 32, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.12 secs
Fri Jan  6 11:00:17 2023: Image # 85, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.01 secs
Fri Jan  6 11:00:17 2023: Image # 10, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
F

Fri Jan  6 11:00:18 2023: Image # 54, module MeasureImageIntensity # 5: CPU_time = 0.04 secs, Wall_time = 0.16 secs
Fri Jan  6 11:00:17 2023: Image # 44, module MeasureTexture # 7: CPU_time = 3.55 secs, Wall_time = 0.45 secs
Fri Jan  6 11:00:18 2023: Image # 44, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:18 2023: Image # 44, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:18 2023: Image # 21, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.25 secs
Fri Jan  6 11:00:18 2023: Image # 99, module MeasureTexture # 7: CPU_time = 2.47 secs, Wall_time = 0.23 secs
Fri Jan  6 11:00:18 2023: Image # 99, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:18 2023: Image # 99, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:18 2023: Image # 33, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time 

In [12]:
patch_feature_output_path=f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/FeatureResults/PatchFeature"
patch_cp.compute_image_features(output_path=patch_feature_output_path,
                                number_of_kernels=imspire_param.CellProfilerParam_KernelNumber)
patch_cp.filter_image_features(output_path=patch_feature_output_path)

/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper
Experiment-wide values for mean threshold, etc calculated by MeasureImageQuality may be incorrect if the run is split into subsets of images.
Given the large number of image sets, you may want to consider using ExportToDatabase as opposed to ExportToSpreadsheet.
/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to u

Fri Jan  6 11:00:30 2023: Image # 1657, module NamesAndTypes # 3: CPU_time = 1.60 secs, Wall_time = 0.84 secs
Fri Jan  6 11:00:31 2023: Image # 1657, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:30 2023: Image # 1450, module NamesAndTypes # 3: CPU_time = 1.50 secs, Wall_time = 0.82 secs
Fri Jan  6 11:00:31 2023: Image # 1450, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:30 2023: Image # 1, module NamesAndTypes # 3: CPU_time = 1.50 secs, Wall_time = 0.81 secs
Fri Jan  6 11:00:31 2023: Image # 1, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:31 2023: Image # 1657, module MeasureImageIntensity # 5: CPU_time = 0.07 secs, Wall_time = 0.04 secs
Fri Jan  6 11:00:31 2023: Image # 1450, module MeasureImageIntensity # 5: CPU_time = 0.04 secs, Wall_time = 0.03 secs
Fri Jan  6 11:00:30 2023: Image # 829, module NamesAndTypes # 3: CPU_time = 1.54 secs, Wall_time = 0.79 secs
Fri Jan  6 11:00:31 20

Fri Jan  6 11:00:31 2023: Image # 415, module MeasureTexture # 7: CPU_time = 1.17 secs, Wall_time = 0.15 secs
Fri Jan  6 11:00:32 2023: Image # 415, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 415, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 416, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 416, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:31 2023: Image # 622, module MeasureTexture # 7: CPU_time = 0.78 secs, Wall_time = 0.14 secs
Fri Jan  6 11:00:32 2023: Image # 622, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 622, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 623, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:3

Fri Jan  6 11:00:33 2023: Image # 3, module MeasureImageQuality # 6: CPU_time = 0.12 secs, Wall_time = 0.06 secs
Fri Jan  6 11:00:32 2023: Image # 1658, module MeasureTexture # 7: CPU_time = 6.84 secs, Wall_time = 1.08 secs
Fri Jan  6 11:00:33 2023: Image # 1658, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:33 2023: Image # 1658, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:33 2023: Image # 1659, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:33 2023: Image # 1659, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:32 2023: Image # 1037, module MeasureTexture # 7: CPU_time = 4.96 secs, Wall_time = 0.77 secs
Fri Jan  6 11:00:33 2023: Image # 1037, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:33 2023: Image # 1037, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs

Fri Jan  6 11:00:34 2023: Image # 1245, module MeasureImageQuality # 6: CPU_time = 0.22 secs, Wall_time = 0.34 secs
Fri Jan  6 11:00:34 2023: Image # 1038, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.06 secs
Fri Jan  6 11:00:34 2023: Image # 832, module NamesAndTypes # 3: CPU_time = 0.76 secs, Wall_time = 0.60 secs
Fri Jan  6 11:00:34 2023: Image # 832, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:34 2023: Image # 832, module MeasureImageIntensity # 5: CPU_time = 0.03 secs, Wall_time = 0.03 secs
Fri Jan  6 11:00:34 2023: Image # 1866, module MeasureTexture # 7: CPU_time = 6.15 secs, Wall_time = 0.84 secs
Fri Jan  6 11:00:34 2023: Image # 1866, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:34 2023: Image # 1866, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:00:34 2023: Image # 1867, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 se

...

Fri Jan  6 11:04:29 2023: Image # 1854, module MeasureTexture # 7: CPU_time = 3.02 secs, Wall_time = 0.41 secs
Fri Jan  6 11:04:29 2023: Image # 1854, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 1854, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 1855, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 1855, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 1447, module MeasureTexture # 7: CPU_time = 4.94 secs, Wall_time = 0.54 secs
Fri Jan  6 11:04:29 2023: Image # 1447, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 1447, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:29 2023: Image # 2068, module MeasureTexture # 7: CPU_time = 3.37 secs, Wall_time = 0.42 secs
F

Fri Jan  6 11:04:30 2023: Image # 825, module MeasureImageQuality # 6: CPU_time = 0.05 secs, Wall_time = 0.08 secs
Fri Jan  6 11:04:30 2023: Image # 194, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.10 secs
Fri Jan  6 11:04:30 2023: Image # 194, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.05 secs
Fri Jan  6 11:04:30 2023: Image # 1856, module NamesAndTypes # 3: CPU_time = 0.40 secs, Wall_time = 0.35 secs
Fri Jan  6 11:04:31 2023: Image # 1856, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:31 2023: Image # 1856, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.06 secs
Fri Jan  6 11:04:31 2023: Image # 1856, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.21 secs
Fri Jan  6 11:04:30 2023: Image # 1652, module MeasureTexture # 7: CPU_time = 6.42 secs, Wall_time = 0.64 secs
Fri Jan  6 11:04:31 2023: Image # 1652, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, W

Fri Jan  6 11:04:32 2023: Image # 1654, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.06 secs
Fri Jan  6 11:04:32 2023: Image # 1858, module NamesAndTypes # 3: CPU_time = 0.73 secs, Wall_time = 0.17 secs
Fri Jan  6 11:04:32 2023: Image # 1858, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:32 2023: Image # 1858, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.12 secs
Fri Jan  6 11:04:32 2023: Image # 196, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.17 secs
Fri Jan  6 11:04:32 2023: Image # 827, module MeasureTexture # 7: CPU_time = 7.81 secs, Wall_time = 0.45 secs
Fri Jan  6 11:04:32 2023: Image # 827, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:32 2023: Image # 827, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:32 2023: Image # 828, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs

Fri Jan  6 11:04:33 2023: Image # 1860, module MeasureTexture # 7: CPU_time = 3.85 secs, Wall_time = 0.21 secs
Fri Jan  6 11:04:33 2023: Image # 1860, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 1860, module CreateBatchFiles # 9: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 1861, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 1861, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 198, module MeasureTexture # 7: CPU_time = 3.75 secs, Wall_time = 0.25 secs
Fri Jan  6 11:04:33 2023: Image # 198, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 198, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:33 2023: Image # 199, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11

Fri Jan  6 11:04:35 2023: Image # 203, module MeasureTexture # 7: CPU_time = 3.70 secs, Wall_time = 0.12 secs
Fri Jan  6 11:04:35 2023: Image # 203, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:35 2023: Image # 203, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:35 2023: Image # 204, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:35 2023: Image # 204, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:35 2023: Image # 204, module NamesAndTypes # 3: CPU_time = 0.71 secs, Wall_time = 0.07 secs
Fri Jan  6 11:04:35 2023: Image # 204, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:04:35 2023: Image # 204, module MeasureImageIntensity # 5: CPU_time = 0.01 secs, Wall_time = 0.02 secs
Fri Jan  6 11:04:35 2023: Image # 204, module MeasureImageQuality # 6: CPU_time = 0.04 secs, Wall_time = 0.04 secs
Fri Jan  6 11:

In [13]:
spot_features=spot_cp.image_features.loc[imdata.pos_in_tissue_filter.index,]

patch_cp.image_features.index=patch_cp.image_features.index.astype('int')
patch_features=patch_cp.image_features.sort_index()
patch_features.index=list(range(patch_features.shape[0]))

spot_features.to_csv(f"{spot_feature_output_path}/Image_Features_Image_filter.txt", sep = "\t")
patch_features.to_csv(f"{patch_feature_output_path}/Image_Features_Image_filter.txt", sep = "\t")

In [14]:
spot_locations=np.array(imdata.pos_in_tissue_filter.loc[:,["pxl_row_in_fullres","pxl_col_in_fullres"]])
patch_locations=np.array(im.patch_in_tissue.loc[:,["pxl_row","pxl_col"]])

In [15]:
spot_feature=pd.read_csv(f"{spot_feature_output_path}/Image_Features_Image_filter.txt",sep="\t",index_col=0)
patch_feature=pd.read_csv(f"{patch_feature_output_path}/Image_Features_Image_filter.txt",sep="\t",index_col=0)

## make sure spot features and patch features have the same dimension
spot_feature=spot_feature.dropna(axis=1)
patch_feature=patch_feature.dropna(axis=1)
commom_feature=list(set(spot_feature.columns).intersection(set(patch_feature.columns)))
spot_feature = spot_feature.loc[:,commom_feature]
patch_feature = patch_feature.loc[:,commom_feature]

spot_feature=np.array(spot_feature.loc[imdata.pos_in_tissue_filter.index,])
patch_feature=np.array(patch_feature.sort_index())

In [16]:
exp_data=imdata.adata.to_df()
exp_data=exp_data.loc[imdata.pos_in_tissue_filter.index,]

In [17]:
ot_solver=imspire.ImSpiRE_OT_Solver(spot_locations,patch_locations,
                                    spot_image_features=spot_feature,
                                    patch_image_features=patch_feature,
                                    spot_gene_expression=exp_data,
                                    random_state=imspire_param.BasicParam_RandomState)

In [18]:
ot_solver.setup_cost_matrices(alpha=imspire_param.OptimalTransportParam_Alpha,
                              num_neighbors=imspire_param.OptimalTransportParam_NumNeighbors)
ot_solver.solve_OT(beta=imspire_param.OptimalTransportParam_Beta, 
                   epsilon=imspire_param.OptimalTransportParam_Epsilon,
                   numItermax=imspire_param.OptimalTransportParam_NumIterMax,
                   verbose=imspire_param.BasicParam_Verbose)

In [19]:
exp_data_hr=imspire.compute_high_resolution_expression_profiles(exp_data,ot_solver.T)

In [20]:
## output results
im.patch_in_tissue.index=list(range(im.patch_in_tissue.shape[0]))
im.patch_in_tissue.to_csv(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/{imspire_param.BasicParam_OutputName}_PatchLocations.txt", sep = "\t")

adata_hr=sc.AnnData(exp_data_hr)
adata_hr.write_h5ad(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/{imspire_param.BasicParam_OutputName}_ResolutionEnhancementResult.h5ad")

np.save(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/SupplementaryResults/ot_M_alpha{imspire_param.OptimalTransportParam_Alpha}_beta{imspire_param.OptimalTransportParam_Beta}_epsilon{imspire_param.OptimalTransportParam_Epsilon}.npy",ot_solver.M)
np.save(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/SupplementaryResults/ot_C1_alpha{imspire_param.OptimalTransportParam_Alpha}_beta{imspire_param.OptimalTransportParam_Beta}_epsilon{imspire_param.OptimalTransportParam_Epsilon}.npy",ot_solver.C1)
np.save(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/SupplementaryResults/ot_C2_alpha{imspire_param.OptimalTransportParam_Alpha}_beta{imspire_param.OptimalTransportParam_Beta}_epsilon{imspire_param.OptimalTransportParam_Epsilon}.npy",ot_solver.C2)
np.save(f"{imspire_param.BasicParam_OutputDir}/{imspire_param.BasicParam_OutputName}/SupplementaryResults/ot_T_alpha{imspire_param.OptimalTransportParam_Alpha}_beta{imspire_param.OptimalTransportParam_Beta}_epsilon{imspire_param.OptimalTransportParam_Epsilon}.npy",ot_solver.T)

#### 3.3.2 one step

In [21]:
imspire_run=imspire.ImSpiRE(imspire_param)

In [22]:
imspire_run.run()

The project .//test_output exists! ImSpaRE overwrite it.
The folder .//test_output exists!
The folder .//test_output/ImageResults exists!
The folder .//test_output/ImageResults/SpotImage exists!
The folder .//test_output/ImageResults/PatchImage exists!
The folder .//test_output/FeatureResults exists!
The folder .//test_output/FeatureResults/SpotFeature exists!
The folder .//test_output/FeatureResults/PatchFeature exists!
The folder .//test_output/SupplementaryResults exists!
.//test_output/SupplementaryResults/bgremover_output.png


/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper
Experiment-wide values for mean threshold, etc calculated by MeasureImageQuality may be incorrect if the run is split into subsets of images.
/mnt/Storage/home/zhangyizhi/anaconda3/envs/test_imspire/lib/python3.8/site-packages/skimage/io/manage_plugins.py:23: UserWarning: Your installed pillow version is < 8.1.2. Several security issues (CVE-2021-27921, CVE-2021-25290, CVE-2021-25291, CVE-2021-25293, and more) have been fixed in pillow 8.1.2 or higher. We recommend to upgrade this library.
  from .collection import imread_collection_wrapper
Experiment-wide values for mean threshold, etc c

Fri Jan  6 11:05:21 2023: Image # 23, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:21 2023: Image # 23, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:20 2023: Image # 12, module NamesAndTypes # 3: CPU_time = 1.71 secs, Wall_time = 0.93 secs
Fri Jan  6 11:05:21 2023: Image # 12, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:21 2023: Image # 56, module NamesAndTypes # 3: CPU_time = 1.52 secs, Wall_time = 0.80 secs
Fri Jan  6 11:05:20 2023: Image # 1, module NamesAndTypes # 3: CPU_time = 1.59 secs, Wall_time = 0.89 secs
Fri Jan  6 11:05:21 2023: Image # 1, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:21 2023: Image # 56, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:21 2023: Image # 12, module MeasureImageIntensity # 5: CPU_time = 0.05 secs, Wall_time = 0.03 secs
Fri Jan  6 11:05:21 2023: Image # 1, module MeasureImag

Fri Jan  6 11:05:22 2023: Image # 24, module NamesAndTypes # 3: CPU_time = 1.37 secs, Wall_time = 0.40 secs
Fri Jan  6 11:05:22 2023: Image # 24, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:22 2023: Image # 89, module MeasureTexture # 7: CPU_time = 1.48 secs, Wall_time = 0.31 secs
Fri Jan  6 11:05:22 2023: Image # 89, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:22 2023: Image # 89, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:22 2023: Image # 90, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:22 2023: Image # 90, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:22 2023: Image # 24, module MeasureImageIntensity # 5: CPU_time = 0.08 secs, Wall_time = 0.04 secs
Fri Jan  6 11:05:22 2023: Image # 13, module NamesAndTypes # 3: CPU_time = 2.04 secs, Wall_time = 0.58 secs
Fri Jan  6 11:05:22 2023: Ima

Fri Jan  6 11:05:24 2023: Image # 69, module MeasureImageQuality # 6: CPU_time = 0.10 secs, Wall_time = 0.06 secs
Fri Jan  6 11:05:23 2023: Image # 101, module MeasureTexture # 7: CPU_time = 7.89 secs, Wall_time = 0.77 secs
Fri Jan  6 11:05:24 2023: Image # 101, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:23 2023: Image # 58, module NamesAndTypes # 3: CPU_time = 1.30 secs, Wall_time = 0.84 secs
Fri Jan  6 11:05:24 2023: Image # 101, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:24 2023: Image # 58, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:24 2023: Image # 102, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:23 2023: Image # 3, module NamesAndTypes # 3: CPU_time = 1.68 secs, Wall_time = 0.71 secs
Fri Jan  6 11:05:24 2023: Image # 3, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:05:24 2023: Image

...

Fri Jan  6 11:09:46 2023: Image # 409, module NamesAndTypes # 3: CPU_time = 0.39 secs, Wall_time = 0.33 secs
Fri Jan  6 11:09:46 2023: Image # 409, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:46 2023: Image # 409, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.04 secs
Fri Jan  6 11:09:46 2023: Image # 1236, module MeasureTexture # 7: CPU_time = 3.20 secs, Wall_time = 0.39 secs
Fri Jan  6 11:09:46 2023: Image # 1236, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:46 2023: Image # 1236, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:46 2023: Image # 1237, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:45 2023: Image # 813, module MeasureTexture # 7: CPU_time = 4.48 secs, Wall_time = 0.52 secs
Fri Jan  6 11:09:46 2023: Image # 1237, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:

Fri Jan  6 11:09:47 2023: Image # 1239, module NamesAndTypes # 3: CPU_time = 0.34 secs, Wall_time = 0.15 secs
Fri Jan  6 11:09:47 2023: Image # 1239, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:47 2023: Image # 1239, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.02 secs
Fri Jan  6 11:09:47 2023: Image # 816, module NamesAndTypes # 3: CPU_time = 0.71 secs, Wall_time = 0.09 secs
Fri Jan  6 11:09:47 2023: Image # 202, module NamesAndTypes # 3: CPU_time = 0.25 secs, Wall_time = 0.07 secs
Fri Jan  6 11:09:47 2023: Image # 816, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:47 2023: Image # 202, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:47 2023: Image # 202, module MeasureImageIntensity # 5: CPU_time = 0.01 secs, Wall_time = 0.02 secs
Fri Jan  6 11:09:47 2023: Image # 816, module MeasureImageIntensity # 5: CPU_time = 0.02 secs, Wall_time = 0.02 secs
Fri Jan  6 11

Fri Jan  6 11:09:49 2023: Image # 204, module MeasureImageQuality # 6: CPU_time = 0.06 secs, Wall_time = 0.14 secs
Fri Jan  6 11:09:48 2023: Image # 817, module MeasureTexture # 7: CPU_time = 5.83 secs, Wall_time = 0.37 secs
Fri Jan  6 11:09:48 2023: Image # 1241, module MeasureTexture # 7: CPU_time = 4.23 secs, Wall_time = 0.37 secs
Fri Jan  6 11:09:49 2023: Image # 817, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:49 2023: Image # 817, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:49 2023: Image # 1241, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:49 2023: Image # 1241, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:49 2023: Image # 818, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:49 2023: Image # 1242, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri

Fri Jan  6 11:09:50 2023: Image # 820, module MeasureTexture # 7: CPU_time = 3.52 secs, Wall_time = 0.18 secs
Fri Jan  6 11:09:50 2023: Image # 820, module ExportToSpreadsheet # 8: CPU_time = 0.01 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2023: Image # 820, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2023: Image # 821, module Images # 1: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2023: Image # 821, module Metadata # 2: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2023: Image # 821, module NamesAndTypes # 3: CPU_time = 0.32 secs, Wall_time = 0.13 secs
Fri Jan  6 11:09:50 2023: Image # 821, module Groups # 4: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2023: Image # 207, module MeasureTexture # 7: CPU_time = 5.63 secs, Wall_time = 0.23 secs
Fri Jan  6 11:09:50 2023: Image # 207, module ExportToSpreadsheet # 8: CPU_time = 0.00 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:50 2

Fri Jan  6 11:09:53 2023: Image # 828, module MeasureTexture # 7: CPU_time = 3.80 secs, Wall_time = 0.14 secs
Fri Jan  6 11:09:53 2023: Image # 828, module ExportToSpreadsheet # 8: CPU_time = 0.02 secs, Wall_time = 0.00 secs
Fri Jan  6 11:09:53 2023: Image # 828, module CreateBatchFiles # 9: CPU_time = 0.00 secs, Wall_time = 0.00 secs
